# This notebook used to create SAHI patch, convert coco -> voc and voc -> coco and visualize annotation in fiftyone 

# list of pre-installed library

In [1]:
# 1. sahi     :  pip install sahi
# 2. pascal_voc_writer   : pip install pascal-voc-writer==0.1.4
# 3. fiftyone  : pip install fiftyone
# 4. pycocotools  : pip install pycocotools-windows


# conerting xml to coco

## import and function

In [43]:
import json
import os, sys
import xml.etree.ElementTree as ET


In [46]:
def labelImg_voc2coco(xml_dir,coco_path_with_name,PRE_DEFINE_CATEGORIES = {"_background_": 0}):
    
    images = []
    annotations = []
    categories = []
        
    coco_json = {
    "images":images,  
    "annotations": annotations,                
    "categories": categories
    }
    if PRE_DEFINE_CATEGORIES != None:
        sub_id = 1
    else:
        sub_id =0
    voc_xmls_list = os.listdir(xml_dir)
    converted_num = 0
    image_id = 0
    bbox_id = 0

    for xml_fileName in voc_xmls_list:

#         print("------------------\n")
#         print("xml_fileName : ",xml_fileName)
    
        converted_num += 1
#         sys.stdout.write('\r>> Processing %s, Converting xml %d/%d' % (xml_fileName, converted_num, len(voc_xmls_list)))
#         sys.stdout.flush()

       
        xml_fullName = os.path.join(xml_dir, xml_fileName)
        tree = ET.parse(xml_fullName)
        root = tree.getroot()         
        
        # image: file_name
        filename = get_element(root, 'filename').text.split('.')[0] + '.jpg' 
        # filename = xml_fileName                                                
        
        # image: id
        image_id = image_id + 1
        
        # image: width & height
        size = get_element(root, 'size')
        img_width = int(get_element(size, 'width').text)
        img_height = int(get_element(size, 'height').text)

        # images
        image = {
            'file_name': filename, 
            'id':image_id,
            'width': img_width,
            'height': img_height
            }

        


        for obj in get_elements(root, 'object'):
            # annotation: category_id
            category = get_element(obj, 'name').text
            if category not in PRE_DEFINE_CATEGORIES:
                new_id = len(PRE_DEFINE_CATEGORIES) + 1 -sub_id
                PRE_DEFINE_CATEGORIES[category] = new_id
#                 if category in ['water_tank', 'effluent_tank', 'fuel_tank']:
#                     print("xml_fileName : ",xml_fileName)
            category_id = PRE_DEFINE_CATEGORIES[category]
            

            # annotation: id
            bbox_id += 1

            # annotation: bbox
            bndbox = get_element(obj, 'bndbox')
#             print("len of bndbox : ",bndbox)
            xmin = int(get_element(bndbox, 'xmin').text)
            ymin = int(get_element(bndbox, 'ymin').text)
            xmax = int(get_element(bndbox, 'xmax').text)
            ymax = int(get_element(bndbox, 'ymax').text)
            
            assert(xmax > xmin)
            assert(ymax > ymin)
            bbox_width = abs(xmax - xmin)
            bbox_height = abs(ymax - ymin)

            # annotation: segmentation
            try: 
                seg = list(eval(get_element(obj, 'segmentation').text))
                
            except :
                seg=None
#             print("[xmin, ymin, bbox_width, bbox_height] : ",xmin, ymin, bbox_width, bbox_height)
            annotation = {
                'id': bbox_id,
                'image_id': image_id,
                'category_id': category_id,
#                 'segmentation': [seg],
                'area': bbox_width * bbox_height, 
                'bbox':[xmin, ymin, bbox_width, bbox_height],
                'iscrowd': 0
                }

            coco_json['annotations'].append(annotation)
        if len(get_elements(root, 'object')) !=0:
#             print("not None")
            coco_json['images'].append(image)
        else:
            print(xml_fileName)
    for cat_name,cat_id in PRE_DEFINE_CATEGORIES.items():
        temp_cat = {
                    'id': cat_id,
                    'name': cat_name,
                    'supercategory': 'object',
                    }
        coco_json['categories'].append(temp_cat)
    print('\r')
    print("Num of categories: %s" % len(categories))
    print("Num of images: %s" % len(images))
    print("Num of annotations: %s" % len(annotations))
    print(PRE_DEFINE_CATEGORIES)
   
    with open(coco_path_with_name, 'w') as outfile:  
        outfile.write(json.dumps(coco_json))

def get_elements(root, childElementName):
    elements = root.findall(childElementName)
    return elements


def get_element(root, childElementName):
    element = root.find(childElementName)
    return element




## setting path variables

In [47]:

# If necessary, pre-define category and its id
PRE_DEFINE_CATEGORIES = {"_background_": 0}  # for backgound 
xml_annot_dir = r"D:\work\trackout\usecase\patch_1024\annot"
xml_2_coco_save_path = r"D:\work\trackout\usecase\patch_1024\patch_1024_xml_to_coco.json"

## applying 

In [48]:
print('start convert')
n = labelImg_voc2coco(xml_dir=xml_annot_dir,coco_path_with_name= xml_2_coco_save_path,PRE_DEFINE_CATEGORIES =PRE_DEFINE_CATEGORIES)
print('\nconvert finished!')

start convert

Num of categories: 3
Num of images: 844
Num of annotations: 990
{'_background_': 0, 'tire_marks': 1, 'trackout': 2}

convert finished!


In [18]:
n 

[]

# visualizing using coco file 

In [1]:
import fiftyone as fo

## setting image directory and annotation file

In [8]:
# The directory containing the source images
data_path = r"D:\work\trackout\usecase\patch_1024\Images\\"
# The path to the COCO labels JSON file
labels_path =r"D:/temp_save/sahi/final_test/coco_annot/xml_2_coco.json" 

## visualization

In [9]:
# Import the dataset
dataset = fo.Dataset.from_dir(
    dataset_type=fo.types.COCODetectionDataset,
    data_path=data_path,
    labels_path=labels_path,
)

session = fo.launch_app(dataset)

   8% |█/-----------------|  1/12 [1.7ms elapsed, 17.2ms remaining, 35.7K samples/s]   


KeyError: 'DJI_20211123144922_0004_W.jpg'

# sahi

## importing library

In [5]:
from sahi.slicing import slice_coco
from sahi.utils.file import load_json
import datetime

## dir path to load and save image and annotation for slicing

In [6]:
# path to load data into sahi
img_dir =r"D:\work\trackout\data\imgs\\"
coco_json=r"D:\work\trackout\data\xml_2_coco.json"

# path to save data
img_save_dir =r"D:\work\trackout\usecase\patch_1024\temp_patch\\" 
annot_save_dir =r"D:\work\trackout\usecase\patch_1024\temp_xml\\"


## variable to tune according to use

In [8]:
patch_height = 1024
pathc_width  = 1024
overlap_height_ratio = 0.2 # 20% can overlap to one patch to other patch
overlap_widht_ratio  = 0.2 # 20% can overlap to one patch to other patch
min_area_to_consider =0.4
annot_name = "sliced" # _coco.json is added by sahi while save the json
ignore_negative_patch =  False # patch with does not have object are ignored. 

## applying sahi slicing 

In [9]:
start_time =datetime.datetime.now()
coco_dict, coco_path = slice_coco(
    coco_annotation_file_path = coco_json,
    image_dir = img_dir,
    output_coco_annotation_file_name = annot_name,
    ignore_negative_samples = ignore_negative_patch,
    output_dir = img_save_dir,
    slice_height = patch_height,
    slice_width = pathc_width,
    overlap_height_ratio = overlap_height_ratio,
    overlap_width_ratio = overlap_widht_ratio,
    min_area_ratio= min_area_to_consider,
    verbose=True
)

end_time =datetime.datetime.now()
print("Total time taken (h:m:s:ms)  : ",(end_time - start_time))

indexing coco dataset annotations...


  0%|                                                                                          | 0/370 [00:00<?, ?it/s]11/18/2022 20:28:17 - INFO - sahi.slicing -   image.shape: (4056, 3040)
11/18/2022 20:28:17 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144914_0002_W_0_0_1024_1024.jpg
11/18/2022 20:28:17 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144914_0002_W_1640_0_2664_1024.jpg
11/18/2022 20:28:17 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144914_0002_W_820_0_1844_1024.jpg
11/18/2022 20:28:17 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144914_0002_W_3032_0_4056_1024.jpg
11/18/2022 20:28:17 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144914_0002_W_2460_0_3484_1024.jpg
11/18/2022 20:28:1

11/18/2022 20:28:19 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144922_0004_W_820_820_1844_1844.jpg
11/18/2022 20:28:19 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144922_0004_W_1640_820_2664_1844.jpg
11/18/2022 20:28:19 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144922_0004_W_2460_820_3484_1844.jpg
11/18/2022 20:28:19 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144922_0004_W_820_1640_1844_2664.jpg
11/18/2022 20:28:19 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144922_0004_W_3032_820_4056_1844.jpg
11/18/2022 20:28:19 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144922_0004_W_1640_1640_2664_2664.jpg
11/18/2022 20:28:19 - INFO - sahi.

11/18/2022 20:28:20 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144931_0006_W_0_2016_1024_3040.jpg
11/18/2022 20:28:20 - INFO - sahi.slicing -   Num slices: 20 slice_height: 1024 slice_width: 1024
  1%|█                                                                                 | 5/370 [00:03<04:21,  1.40it/s]11/18/2022 20:28:20 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144931_0006_W_3032_1640_4056_2664.jpg
11/18/2022 20:28:20 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144931_0006_W_820_2016_1844_3040.jpg
11/18/2022 20:28:20 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144931_0006_W_2460_2016_3484_3040.jpg
11/18/2022 20:28:20 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144931_0006_W_1

11/18/2022 20:28:22 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144943_0009_W_1640_0_2664_1024.jpg
11/18/2022 20:28:22 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144943_0009_W_0_0_1024_1024.jpg
11/18/2022 20:28:22 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144943_0009_W_820_0_1844_1024.jpg
11/18/2022 20:28:22 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144943_0009_W_2460_0_3484_1024.jpg
11/18/2022 20:28:22 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144943_0009_W_1640_820_2664_1844.jpg
11/18/2022 20:28:22 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20211123144943_0009_W_3032_0_4056_1024.jpg
11/18/2022 20:28:22 - INFO - sahi.slicing -   sl

...

11/18/2022 20:39:58 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928173725_0011_7168_1640_8192_2664.jpg
11/18/2022 20:39:58 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928173725_0011_820_2460_1844_3484.jpg
11/18/2022 20:39:58 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928173725_0011_0_2460_1024_3484.jpg
11/18/2022 20:39:58 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928173725_0011_2460_2460_3484_3484.jpg
11/18/2022 20:39:58 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928173725_0011_1640_2460_2664_3484.jpg
11/18/2022 20:39:58 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928173725_0011_4100_2460_5124_3484.jpg
11/18/2022 20:39:58 - INFO - sahi.slicing - 

11/18/2022 20:40:00 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_3280_820_4304_1844.jpg
11/18/2022 20:40:00 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_5740_820_6764_1844.jpg
11/18/2022 20:40:00 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_820_820_1844_1844.jpg
11/18/2022 20:40:00 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_1640_820_2664_1844.jpg
11/18/2022 20:40:00 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_4920_820_5944_1844.jpg
11/18/2022 20:40:00 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_4100_820_5124_1844.jpg
11/18/2022 20:40:00 - INFO - sahi.slicing -   s

11/18/2022 20:40:01 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_820_4436_1844_5460.jpg
11/18/2022 20:40:01 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_2460_4436_3484_5460.jpg
11/18/2022 20:40:01 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_3280_4436_4304_5460.jpg
11/18/2022 20:40:01 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_4100_4436_5124_5460.jpg
11/18/2022 20:40:01 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_4920_4436_5944_5460.jpg
11/18/2022 20:40:01 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928174638_0062_6560_4436_7584_5460.jpg
11/18/2022 20:40:01 - INFO - sahi.slicing

11/18/2022 20:40:03 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928175758_0125_1640_3280_2664_4304.jpg
11/18/2022 20:40:03 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928175758_0125_3280_3280_4304_4304.jpg
11/18/2022 20:40:03 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928175758_0125_2460_3280_3484_4304.jpg
11/18/2022 20:40:03 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928175758_0125_4100_3280_5124_4304.jpg
11/18/2022 20:40:03 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928175758_0125_4920_3280_5944_4304.jpg
11/18/2022 20:40:03 - INFO - sahi.slicing -   sliced image path: D:\work\trackout\usecase\patch_1024\temp_patch\DJI_20220928175758_0125_5740_3280_6764_4304.jpg
11/18/2022 20:40:03 - INFO - sahi.slicin

Total time taken (h:m:s:ms)  :  0:11:47.075490


## moving annoation to annot folder (optional)

In [14]:
import shutil
import os

In [16]:
file_path = img_save_dir+annot_name+"_coco.json"
# print("file_path : ",file_path)
if os.path.exists(file_path):
    shutil.move(file_path,annot_save_dir)
    print("file : {} moved to -> {}".format(file_path,annot_save_dir))
else:
    print("path not exist")

file : D:\temp_save\sahi\final_test\sliced_imgs\\sliced_coco.json moved to -> D:\temp_save\sahi\final_test\sliced_annot\\


#  Converstion coco to xml

## importing and function 

In [10]:
from pycocotools.coco import COCO
from pascal_voc_writer import Writer
import argparse
import os

In [11]:
def convert_coco2voc(annot_file, output_dir):
    coco = COCO(annot_file)
    cats = coco.loadCats(coco.getCatIds())
    cat_idx = {}
    for c in cats:
        cat_idx[c['id']] = c['name']
    for img in coco.imgs:
        catIds = coco.getCatIds()
        annIds = coco.getAnnIds(imgIds=[img], catIds=catIds)
        if len(annIds) > 0:
            img_fname = coco.imgs[img]['file_name']
            image_fname_ls = img_fname.split('.')
            image_fname_ls[-1] = 'xml'
            label_fname = '.'.join(image_fname_ls)
            writer = Writer(img_fname, coco.imgs[img]['width'], coco.imgs[img]['height'])
            anns = coco.loadAnns(annIds)
            for a in anns:
                bbox = a['bbox']
                bbox = [bbox[0], bbox[1], bbox[2] + bbox[0], bbox[3] + bbox[1]]
                bbox = [str(b) for b in bbox]
                catname = cat_idx[a['category_id']]
                writer.addObject(catname, bbox[0], bbox[1], bbox[2], bbox[3])
                writer.save(output_dir+'/'+label_fname)


## setting file name and dir

In [12]:
output_dir = r"D:\work\trackout\usecase\patch_1024\temp_xml"
annot_file = r"D:\work\trackout\usecase\patch_1024\temp_patch\sliced_coco.json"

## applying convertion and saving the xml file 

In [13]:
convert_coco2voc(annot_file=annot_file,output_dir=output_dir)

loading annotations into memory...
Done (t=0.06s)
creating index...
index created!


# visualizing using xml file 

In [38]:
import fiftyone as fo

## setting image directory and annotation file

In [39]:
# The directory containing the source images
data_path = r"D:\work\trackout\usecase\patch_1024\Images"
# The dir path to the xml file
labels_path =  r"D:\work\trackout\usecase\patch_1024\annot"

## visualization

In [42]:
# Import the dataset
dataset = fo.Dataset.from_dir(
    dataset_type=fo.types.VOCDetectionDataset,
    data_path=data_path,
    labels_path=labels_path,
)

session = fo.launch_app(dataset)

 100% |█████████████████| 844/844 [1.2s elapsed, 0s remaining, 698.6 samples/s]         


# stats generation

In [52]:
import json
import glob
import pandas as pd

In [53]:
def get_cat_id_info(cat_id_list):
    cat_2_id,id_2_cat ={},{}
    for item in cat_id_list:
        cat_2_id[item["name"]] = item["id"]
        id_2_cat[item["id"]] = item["name"]
    return cat_2_id, id_2_cat

def get_stats(lst):
    min_data = np.min(lst)
    max_data =np.max(lst)
    mean_data =np.mean(lst)
    std_data =np.std(lst)
    return min_data,max_data,round(mean_data,2),round(std_data,3)
    
def find_area_width_height(box,annot_format="coco"):
    
    if annot_format =="coco":
        x1,y1,w,h = box[0:4]
        
    if annot_format =="voc":
        x1,y1,x2,y2 = box[0:4]
        w=np.abs(x1-x2)
        h=np.abs(y1-y2)
        
    return int(w),int(h),int(w*h)
        
def print_stats(annot_dict):
    df=pd.DataFrame(columns=['class_name','total_count','min_width','max_width','mean_width','std_width',
                        'min_height','max_height','mean_height','std_height',
                        'min_area','max_area','mean_area','std_area'])
    
    print("----------------------- stats -------------------------------")
    print("total category : ",len(annot_dict["cat_ids"]))
    print("category IDS: \n",annot_dict["cat_ids"])
    print("category names: \n",annot_dict["cat_names"])
    print("classwise distribution : ")
    for key,value in annot_dict["class_info"].items():
        if key=="_background_":
            continue
        value =value[0]
        print("\t{} : Total = {} ".format(key,value["total_count"]))
        print("")
        print("\tmin width : {}, max width {}, mean : {}, std : {} ".format(*value["width"]))
        print("\tmin height : {}, max height {}, mean : {}, std : {} ".format(*value["height"]))
        print("\tmin area : {}, max area {}, mean : {}, std : {} ".format(*value["area"]))
#         total_info.append([value["total_count"],value["width"][0],value["height"][0],value["area"][0]])
#         total_count=total_count+value["total_count"]
        print("\n\t----------------------------------------------------------------------")
        df.loc[len(df.index)] = [key,value["total_count"],*value["width"],*value["height"],*value["area"]]
    
    
    print("Total bounding box : ",annot_dict["total_count"])
    print("min width : {}, max width {}, mean : {}, std : {} ".format(*annot_dict["total_width"]))
    print("min height : {}, max height {}, mean : {}, std : {} ".format(*annot_dict["total_height"]))
    print("min area : {}, max area {}, mean : {}, std : {} ".format(*annot_dict["total_area"]))
    print("\n----------------------------------------------------------------------")
    df.loc[len(df.index)] = ["Total",annot_dict["total_count"],*annot_dict["total_width"],*annot_dict["total_height"],*annot_dict["total_area"]]
    return df
import pandas as pd
def get_annotation_stats(path, annot_format="coco"):  # 'voc',"yolo"
    
    
    if annot_format == "coco":
        with open(path, 'r') as file:
            json_data = json.load(file)
        cat_2_id, id_2_cat = get_cat_id_info(json_data["categories"])
        info = {}
        info["cat_ids"] = list(cat_2_id.values())
        info["cat_names"] = list(cat_2_id.keys())
        info["class_info"] = {i: [] for i in cat_2_id.keys()}
        cat_id_info = {i: [] for i in id_2_cat.keys()}
        for item in json_data["annotations"]:
            width, height, area = find_area_width_height(item["bbox"])
            cat_id_info[item["category_id"]].append([width, height, area])
        total_count =0
        t_width,t_height,t_area=[],[],[]
        for ids, lst in cat_id_info.items():
            if len(lst)==0: # for background _background_ == we have zero list
                continue
            temp = {}
            temp["cat_name"] = ids 
            temp['total_count'] = len(lst)
            total_count = total_count+ len(lst)
            temp["width"] = get_stats([box[0] for box in lst])
            t_width.extend([box[0] for box in lst])
            
            temp["height"] = get_stats([box[1] for box in lst])
            t_height.extend([box[1] for box in lst])
            
            temp["area"] = get_stats([box[2] for box in lst])
            t_area.extend([box[2] for box in lst])
            
            info["class_info"][id_2_cat[ids]].append(temp)
            
        info["total_count"]=total_count
        info['total_width'] = get_stats(t_width)
        info['total_height'] = get_stats(t_height)
        info['total_area'] = get_stats(t_area)
#         print(info.keys())
        return print_stats(info)

In [54]:
train_track_json_path = r"D:\work\trackout\usecase\patch_1024\train.json"
test_track_json_path = r"D:\work\trackout\usecase\patch_1024\test.json"

In [55]:
train_trackout_df = get_annotation_stats(train_track_json_path, annot_format="coco")

----------------------- stats -------------------------------
total category :  3
category IDS: 
 [0, 1, 2]
category names: 
 ['_background_', 'tire_marks', 'trackout']
classwise distribution : 
	tire_marks : Total = 399 

	min width : 77, max width 515, mean : 235.49, std : 93.288 
	min height : 52, max height 470, mean : 183.34, std : 74.167 
	min area : 6500, max area 172380, mean : 44609.59, std : 29817.451 

	----------------------------------------------------------------------
	trackout : Total = 393 

	min width : 87, max width 695, mean : 255.5, std : 95.379 
	min height : 61, max height 484, mean : 222.52, std : 77.305 
	min area : 10890, max area 208071, mean : 57156.87, std : 30296.598 

	----------------------------------------------------------------------
Total bounding box :  792
min width : 77, max width 695, mean : 245.42, std : 94.86 
min height : 52, max height 484, mean : 202.78, std : 78.233 
min area : 6500, max area 208071, mean : 50835.7, std : 30703.896 

----

In [56]:
test_trackout_df = get_annotation_stats(test_track_json_path, annot_format="coco")

----------------------- stats -------------------------------
total category :  3
category IDS: 
 [0, 1, 2]
category names: 
 ['_background_', 'tire_marks', 'trackout']
classwise distribution : 
	tire_marks : Total = 131 

	min width : 74, max width 460, mean : 202.06, std : 83.753 
	min height : 54, max height 359, mean : 151.28, std : 55.46 
	min area : 8346, max area 158319, mean : 31067.64, std : 21113.939 

	----------------------------------------------------------------------
	trackout : Total = 67 

	min width : 106, max width 514, mean : 278.27, std : 102.988 
	min height : 97, max height 344, mean : 211.97, std : 66.801 
	min area : 12614, max area 148546, mean : 61452.72, std : 34561.903 

	----------------------------------------------------------------------
Total bounding box :  198
min width : 74, max width 514, mean : 227.85, std : 97.623 
min height : 54, max height 359, mean : 171.82, std : 66.103 
min area : 8346, max area 158319, mean : 41349.46, std : 30097.4 

---

# rought

## conerting xml to coco

In [ ]:
# Import the dataset
dataset = fo.Dataset.from_dir(
    dataset_type=fo.types.COCODetectionDataset,
    data_path=data_path,
    labels_path=labels_path,
)

session = fo.launch_app(dataset)

In [ ]:
import json
import os, sys
import xml.etree.ElementTree as ET


In [ ]:
def labelImg_voc2coco(xml_dir,coco_path_with_name,PRE_DEFINE_CATEGORIES = {"_background_": 0}):
    
    images = []
    annotations = []
    categories = []
        
    coco_json = {
    "images":images,  
    "annotations": annotations,                
    "categories": categories
    }
    if PRE_DEFINE_CATEGORIES != None:
        sub_id = 1
    else:
        sub_id =0
    voc_xmls_list = os.listdir(xml_dir)
    converted_num = 0
    image_id = 0
    bbox_id = 0

    for xml_fileName in voc_xmls_list:
        
    
        converted_num += 1
        sys.stdout.write('\r>> Processing %s, Converting xml %d/%d' % (xml_fileName, converted_num, len(voc_xmls_list)))
        sys.stdout.flush()

       
        xml_fullName = os.path.join(xml_dir, xml_fileName)
        tree = ET.parse(xml_fullName)
        root = tree.getroot()         
        
        # image: file_name
        filename = get_element(root, 'filename').text.split('.')[0] + '.jpg' 
        # filename = xml_fileName                                                
        
        # image: id
        image_id = image_id + 1
        
        # image: width & height
        size = get_element(root, 'size')
        img_width = int(get_element(size, 'width').text)
        img_height = int(get_element(size, 'height').text)

        # images
        image = {
            'file_name': filename, 
            'id':image_id,
            'width': img_width,
            'height': img_height
            }

        coco_json['images'].append(image)


        for obj in get_elements(root, 'object'):
            # annotation: category_id
            category = get_element(obj, 'name').text
            if category not in PRE_DEFINE_CATEGORIES:
                new_id = len(PRE_DEFINE_CATEGORIES) + 1 -sub_id
                PRE_DEFINE_CATEGORIES[category] = new_id
            category_id = PRE_DEFINE_CATEGORIES[category]
            

            # annotation: id
            bbox_id += 1

            # annotation: bbox
            bndbox = get_element(obj, 'bndbox')
            xmin = int(get_element(bndbox, 'xmin').text)
            ymin = int(get_element(bndbox, 'ymin').text)
            xmax = int(get_element(bndbox, 'xmax').text)
            ymax = int(get_element(bndbox, 'ymax').text)
            assert(xmax > xmin)
            assert(ymax > ymin)
            bbox_width = abs(xmax - xmin)
            bbox_height = abs(ymax - ymin)

            # annotation: segmentation
            try: 
                seg = list(eval(get_element(obj, 'segmentation').text))
                
            except :
                seg=None
            annotation = {
                'id': bbox_id,
                'image_id': image_id,
                'category_id': category_id,
                'segmentation': [seg],
                'area': bbox_width * bbox_height, 
                'bbox':[xmin, ymin, bbox_width, bbox_height],
                'iscrowd': 0
                }

            coco_json['annotations'].append(annotation)
    
    for cat_name,cat_id in PRE_DEFINE_CATEGORIES.items():
        temp_cat = {
                    'id': cat_id,
                    'name': cat_name,
                    'supercategory': 'object',
                    }
        coco_json['categories'].append(temp_cat)
    print('\r')
    print("Num of categories: %s" % len(categories))
    print("Num of images: %s" % len(images))
    print("Num of annotations: %s" % len(annotations))
    print(PRE_DEFINE_CATEGORIES)
   
    with open(coco_path_with_name, 'w') as outfile:  
        outfile.write(json.dumps(coco_json))


def get_elements(root, childElementName):
    elements = root.findall(childElementName)
    return elements


def get_element(root, childElementName):
    element = root.find(childElementName)
    return element




In [ ]:

# If necessary, pre-define category and its id
PRE_DEFINE_CATEGORIES = {"_background_": 0}  # for backgound 
xml_annot_dir = r"D:\temp_save\sahi\final_test\voc_annot\\"
xml_2_coco_save_path = r"D:\temp_save\sahi\final_test\coco_annot\xml_2_coco.json"

In [ ]:
print('start convert')
labelImg_voc2coco(xml_dir=xml_annot_dir,coco_path_with_name= xml_2_coco_save_path,PRE_DEFINE_CATEGORIES)
print('\nconvert finished!')

## visualizing using coco file 

In [ ]:
import fiftyone as fo

## setting image directory and annotation file

In [ ]:
# The directory containing the source images
data_path = r"D:\temp_save\sahi\with_negative_frame\imgs"
# The path to the COCO labels JSON file
labels_path = r"D:\temp_save\sahi\with_negative_frame\annot\sliced_coco.json_coco.json"

## visualization

In [ ]:
# Import the dataset
dataset = fo.Dataset.from_dir(
    dataset_type=fo.types.VOCDetectionDataset,
    data_path=data_path,
    labels_path=labels_path,
)

session = fo.launch_app(dataset)

In [8]:
from pycocotools.coco import COCO
from pascal_voc_writer import Writer
import argparse
import os

In [9]:
def coco2voc(ann_file, output_dir):
    coco = COCO(ann_file)
    cats = coco.loadCats(coco.getCatIds())
    cat_idx = {}
    for c in cats:
        cat_idx[c['id']] = c['name']
    for img in coco.imgs:
        catIds = coco.getCatIds()
        annIds = coco.getAnnIds(imgIds=[img], catIds=catIds)
        if len(annIds) > 0:
            img_fname = coco.imgs[img]['file_name']
            image_fname_ls = img_fname.split('.')
            image_fname_ls[-1] = 'xml'
            label_fname = '.'.join(image_fname_ls)
            writer = Writer(img_fname, coco.imgs[img]['width'], coco.imgs[img]['height'])
            anns = coco.loadAnns(annIds)
            for a in anns:
                bbox = a['bbox']
                bbox = [bbox[0], bbox[1], bbox[2] + bbox[0], bbox[3] + bbox[1]]
                bbox = [str(b) for b in bbox]
                catname = cat_idx[a['category_id']]
                writer.addObject(catname, bbox[0], bbox[1], bbox[2], bbox[3])
                writer.save(output_dir+'/'+label_fname)


In [10]:
output_dir = r"D:\temp_save\sahi\final_test\voc_annot"
ann_file = r"D:\work\trackout\usecase\patch_1024\temp_patch\sliced_coco.json"

In [11]:
coco2voc(ann_file, output_dir)

loading annotations into memory...
Done (t=0.09s)
creating index...
index created!


In [ ]:
import json
import os, sys
import xml.etree.ElementTree as ET


In [67]:
def labelImg_voc2coco(VOC_XMLS_DIR,COCO_JSON_FILE,PRE_DEFINE_CATEGORIES = {"_background_": 0}):
    
    images = []
    annotations = []
    categories = []
        
    coco_json = {
    "images":images,  
    "annotations": annotations,                
    "categories": categories
    }
    if PRE_DEFINE_CATEGORIES != None:
        sub_id = 1
    else:
        sub_id =0
    voc_xmls_list = os.listdir(VOC_XMLS_DIR)
    converted_num = 0
    image_id = 0
    bbox_id = 0

    for xml_fileName in voc_xmls_list:
        
    
        converted_num += 1
        sys.stdout.write('\r>> Processing %s, Converting xml %d/%d' % (xml_fileName, converted_num, len(voc_xmls_list)))
        sys.stdout.flush()

       
        xml_fullName = os.path.join(VOC_XMLS_DIR, xml_fileName)
        tree = ET.parse(xml_fullName)
        root = tree.getroot()         
        
        # image: file_name
        filename = get_element(root, 'filename').text.split('.')[0] + '.jpg' 
        # filename = xml_fileName                                                
        
        # image: id
        image_id = image_id + 1
        
        # image: width & height
        size = get_element(root, 'size')
        img_width = int(get_element(size, 'width').text)
        img_height = int(get_element(size, 'height').text)

        # images
        image = {
            'file_name': filename, 
            'id':image_id,
            'width': img_width,
            'height': img_height
            }

        coco_json['images'].append(image)

        if get_elements(root, 'object')==[]:
            print(xml_fileName)
        
        for obj in get_elements(root, 'object'):
            # annotation: category_id
            category = get_element(obj, 'name').text
            if category not in PRE_DEFINE_CATEGORIES:
                new_id = len(PRE_DEFINE_CATEGORIES) + 1 -sub_id
                PRE_DEFINE_CATEGORIES[category] = new_id
            category_id = PRE_DEFINE_CATEGORIES[category]
            

            # annotation: id
            bbox_id += 1

            # annotation: bbox
            bndbox = get_element(obj, 'bndbox')
            xmin = int(get_element(bndbox, 'xmin').text)
            ymin = int(get_element(bndbox, 'ymin').text)
            xmax = int(get_element(bndbox, 'xmax').text)
            ymax = int(get_element(bndbox, 'ymax').text)
            assert(xmax > xmin)
            assert(ymax > ymin)
            bbox_width = abs(xmax - xmin)
            bbox_height = abs(ymax - ymin)

            # annotation: segmentation
            try: 
                seg = list(eval(get_element(obj, 'segmentation').text))
                
            except :
                seg=None
            annotation = {
                'id': bbox_id,
                'image_id': image_id,
                'category_id': category_id,
                'segmentation': [seg],
                'area': bbox_width * bbox_height, 
                'bbox':[xmin, ymin, bbox_width, bbox_height],
                'iscrowd': 0
                }

            coco_json['annotations'].append(annotation)
    
    for cat_name,cat_id in PRE_DEFINE_CATEGORIES.items():
        temp_cat = {
                    'id': cat_id,
                    'name': cat_name,
                    'supercategory': 'object',
                    }
        coco_json['categories'].append(temp_cat)
    print('\r')
    print("Num of categories: %s" % len(categories))
    print("Num of images: %s" % len(images))
    print("Num of annotations: %s" % len(annotations))
    print(PRE_DEFINE_CATEGORIES)
   
    with open(COCO_JSON_FILE, 'w') as outfile:  
        outfile.write(json.dumps(coco_json))


def get_elements(root, childElementName):
    elements = root.findall(childElementName)
    return elements


def get_element(root, childElementName):
    element = root.find(childElementName)
    return element




In [68]:

# If necessary, pre-define category and its id
PRE_DEFINE_CATEGORIES = {"_background_": 0}
categories = [
    {
        'id': 1,
        'name': '_background_',
        'supercategory': 'object',
    }
]

VOC_XMLS_DIR = r"D:\temp_save\sahi\final_test\voc_annot\\"
COCO_JSON_FILE = r"D:\temp_save\sahi\final_test\coco_annot\xml_2_coco.json"

In [ ]:
print('start convert')
labelImg_voc2coco(VOC_XMLS_DIR,COCO_JSON_FILE,PRE_DEFINE_CATEGORIES)
print('\nconvert finished!')

# xml

In [49]:
xml_path  =r"C:\Users\z004k7nr\Desktop\test.xml"

In [50]:
import xml.etree.ElementTree as ET
tree = ET.parse(xml_path)
root = tree.getroot()

In [51]:
get_elements

<Element 'data' at 0x000001EF7FE29EF0>

In [77]:
l = """DJI_20211123144956_0012_W.JPG
DJI_20211123145114_0031_W.JPG
DJI_20211123145118_0032_W.JPG
DJI_20220120124829_0091.JPG
DJI_20220120124932_0105.JPG
DJI_20220120124937_0106.JPG
DJI_20220120124942_0107.JPG
DJI_20220120124947_0108.JPG
DJI_20220120124951_0109.JPG
DJI_20220120124956_0110.JPG
DJI_20220120125010_0113.JPG
DJI_20220120125551_0188.JPG
DJI_20220120125556_0189.JPG
DJI_20220120130705_0335.JPG
DJI_20220120130710_0336.JPG
DJI_20220120131403_0425.JPG
DJI_20220120131407_0426.JPG
DJI_20220120131412_0427.JPG
DJI_20220120142718_0251.JPG
DJI_20220120150142_0037.JPG
DJI_20220307141549_0146.JPG"""

In [78]:
print(l.split("\n"))

['DJI_20211123144956_0012_W.JPG', 'DJI_20211123145114_0031_W.JPG', 'DJI_20211123145118_0032_W.JPG', 'DJI_20220120124829_0091.JPG', 'DJI_20220120124932_0105.JPG', 'DJI_20220120124937_0106.JPG', 'DJI_20220120124942_0107.JPG', 'DJI_20220120124947_0108.JPG', 'DJI_20220120124951_0109.JPG', 'DJI_20220120124956_0110.JPG', 'DJI_20220120125010_0113.JPG', 'DJI_20220120125551_0188.JPG', 'DJI_20220120125556_0189.JPG', 'DJI_20220120130705_0335.JPG', 'DJI_20220120130710_0336.JPG', 'DJI_20220120131403_0425.JPG', 'DJI_20220120131407_0426.JPG', 'DJI_20220120131412_0427.JPG', 'DJI_20220120142718_0251.JPG', 'DJI_20220120150142_0037.JPG', 'DJI_20220307141549_0146.JPG']


In [22]:
def copy_images_and_annot_dir(annot_dir,img_dir,save_annot_dir,save_img_dir):
    import glob
    import os
    import shutil
    file_not_found_list =[]
#     annot_name_list = [annot_name.split("\\")[-1] for annot_name in glob.glob(annot_dir +"\*.xml")].
    annot_file_list =glob.glob(annot_dir +"\*.xml")
    img_name_list = [f.split("\\")[-1] for f in glob.glob(img_dir+"\*.JPG")]
    
    print("lenght annot_name_list : ",len(annot_file_list))
    i=0
    for file_path in annot_file_list:
#         print("file_path :",file_path)
        file_name = file_path.split("\\")[-1]
        file_name =file_name.replace(".xml",".JPG")
        if file_name in ['DJI_20211123144956_0012_W.JPG', 'DJI_20211123145114_0031_W.JPG', 'DJI_20211123145118_0032_W.JPG', 'DJI_20220120124829_0091.JPG', 'DJI_20220120124932_0105.JPG', 'DJI_20220120124937_0106.JPG', 'DJI_20220120124942_0107.JPG', 'DJI_20220120124947_0108.JPG', 'DJI_20220120124951_0109.JPG', 'DJI_20220120124956_0110.JPG', 'DJI_20220120125010_0113.JPG', 'DJI_20220120125551_0188.JPG', 'DJI_20220120125556_0189.JPG', 'DJI_20220120130705_0335.JPG', 'DJI_20220120130710_0336.JPG', 'DJI_20220120131403_0425.JPG', 'DJI_20220120131407_0426.JPG', 'DJI_20220120131412_0427.JPG', 'DJI_20220120142718_0251.JPG', 'DJI_20220120150142_0037.JPG', 'DJI_20220307141549_0146.JPG']:
            continue
        if file_name in img_name_list:
            img_path  = os.path.join(img_dir,file_name)
#             print("img_path : ",img_path)
            shutil.copy(img_path, save_img_dir)
            shutil.copy(file_path, save_annot_dir)
        else:
            print("not found : ",file_name)
            file_not_found_list.append(file_path)
#         i+=1
#         if i==10:
#             break
    print("done")
    return file_not_found_list
     

In [21]:
"""given image dir : copy only annotation for image present in img_dir"""

def copy_annot_only(img_dir,annot_dir,save_annot_dir): # image,annot,both
    import glob
    import os
    import shutil
    import xml.etree.ElementTree as ET
    import glob
    
    empty_annot_list,annot_not_found =[],[]
    ext =".jpg"
    image_file_list =glob.glob(img_dir +"\*"+ext)
    annot_name_list = [f.split("\\")[-1] for f in glob.glob(annot_dir+"\*.xml")]
#     print("annot_name_list : ",annot_name_list[0])
#     print("image_file_list : ",image_file_list[0])
    print("lenght image_file_list : ",len(image_file_list))
    i=0
    for file_path in image_file_list:
        
        file_name = file_path.split("\\")[-1]
        file_name =file_name.replace(ext,".xml")
#         print("file_name : ",file_name)
       
        if file_name in annot_name_list:
            annot_path  = os.path.join(annot_dir,file_name)
              #-----------checking for empty xml file-------------------#
            tree = ET.parse(annot_path)
            root = tree.getroot()
            elements = root.findall('object')
            if elements==[]:
                empty_annot_list.append(file_name)
                continue
            #---------------------------------------------------------#
            
            shutil.copy(annot_path, save_annot_dir)
        else:
            annot_not_found.append(file_path)

    print("------done-----")
    print("empyt annot {}: \n{}".format(len(empty_annot_list),empty_annot_list))
    print("annot not found {} : \n{}".format(len(annot_not_found),annot_not_found))
    return empty_annot_list,annot_not_found

In [22]:
img_dir =r"D:\work\trackout\usecase\patch_1024\Images"
annot_dir =r"D:\work\trackout\usecase\patch_1024\temp_xml"
save_annot_dir =r"D:\work\trackout\usecase\patch_1024\selected_annot\\"

In [23]:
copy_annot_only(img_dir,annot_dir,save_annot_dir)

lenght image_file_list :  874
------done-----
empyt annot 30: 
['DJI_20220118124155_0305_0_1640_1024_2664.xml', 'DJI_20220118124234_0313_3280_4100_4304_5124.xml', 'DJI_20220118124234_0313_3280_4436_4304_5460.xml', 'DJI_20220118130144_0122_3280_3280_4304_4304.xml', 'DJI_20220118131428_0290_7168_4436_8192_5460.xml', 'DJI_20220118131735_0331_3280_0_4304_1024.xml', 'DJI_20220118133440_0039_4920_1640_5944_2664.xml', 'DJI_20220118133440_0039_4920_2460_5944_3484.xml', 'DJI_20220118133805_0084_6560_2460_7584_3484.xml', 'DJI_20220118153811_0033_5740_1640_6764_2664.xml', 'DJI_20220120122622_0315_0_1640_1024_2664.xml', 'DJI_20220120122823_0341_3280_2460_4304_3484.xml', 'DJI_20220120124321_0024_1640_820_2664_1844.xml', 'DJI_20220120124350_0030_1640_4100_2664_5124.xml', 'DJI_20220120124511_0048_0_2460_1024_3484.xml', 'DJI_20220120130157_0267_5740_2460_6764_3484.xml', 'DJI_20220120130902_0361_1640_820_2664_1844.xml', 'DJI_20220120150113_0031_5740_1640_6764_2664.xml', 'DJI_20220421134855_0022_5740_0_

(['DJI_20220118124155_0305_0_1640_1024_2664.xml',
  'DJI_20220118124234_0313_3280_4100_4304_5124.xml',
  'DJI_20220118124234_0313_3280_4436_4304_5460.xml',
  'DJI_20220118130144_0122_3280_3280_4304_4304.xml',
  'DJI_20220118131428_0290_7168_4436_8192_5460.xml',
  'DJI_20220118131735_0331_3280_0_4304_1024.xml',
  'DJI_20220118133440_0039_4920_1640_5944_2664.xml',
  'DJI_20220118133440_0039_4920_2460_5944_3484.xml',
  'DJI_20220118133805_0084_6560_2460_7584_3484.xml',
  'DJI_20220118153811_0033_5740_1640_6764_2664.xml',
  'DJI_20220120122622_0315_0_1640_1024_2664.xml',
  'DJI_20220120122823_0341_3280_2460_4304_3484.xml',
  'DJI_20220120124321_0024_1640_820_2664_1844.xml',
  'DJI_20220120124350_0030_1640_4100_2664_5124.xml',
  'DJI_20220120124511_0048_0_2460_1024_3484.xml',
  'DJI_20220120130157_0267_5740_2460_6764_3484.xml',
  'DJI_20220120130902_0361_1640_820_2664_1844.xml',
  'DJI_20220120150113_0031_5740_1640_6764_2664.xml',
  'DJI_20220421134855_0022_5740_0_6764_1024.xml',
  'DJI_202

In [34]:
def copy_images_and_annot_dir(annot_dir,img_dir,save_annot_dir,save_img_dir,only_copy): # image,annot,both
    import glob
    import os
    import shutil
    import xml.etree.ElementTree as ET
    import glob
    
    empty_annot_list,img_not_found =[],[]
    annot_file_list =glob.glob(annot_dir +"\*.xml")
    img_name_list = [f.split("\\")[-1] for f in glob.glob(img_dir+"\*.jpg")]
    print("lenght annot_name_list : ",len(annot_file_list))
    i=0
    for file_path in annot_file_list:
        #-----------checking for empty xml file-------------------#
        tree = ET.parse(file_path)
        root = tree.getroot()
        elements = root.findall('object')
        if elements ==[]:
            empty_annot_list.append(file_path)
            continue
        #---------------------------------------------------------#
        
        file_name = file_path.split("\\")[-1]
        file_name =file_name.replace(".xml",".jpg")
        if file_name in img_name_list:
            img_path  = os.path.join(img_dir,file_name)
#             print("img_path : ",img_path)
            if only_copy =='image':
                shutil.copy(img_path, save_img_dir)
            elif only_copy =='both':
                shutil.copy(img_path, save_img_dir)
                shutil.copy(file_path, save_annot_dir)
            else:
                sys.exit("spacify param only_copy-> any of [image,annot,both]")
        else:
            print("not found : ",file_name)
            img_not_found.append(file_path)
#         i+=1
#         if i==10:
#             break
    print("------done-----")
    print("empyt annot {}: \n{}".format(len(empty_annot_list),empty_annot_list))
    print("image not found {} : \n{}".format(len(img_not_found),img_not_found))
    return empty_annot_list,img_not_found

In [35]:
   
img_dir= r"D:\work\trackout\usecase\patch_1024\selected_img"
annot_dir =r"D:\work\trackout\usecase\patch_1024\selected_annot" 

save_annot_dir =r"D:\work\trackout\usecase\patch_1024\temp_xml\\" 
save_img_dir=r"D:\work\trackout\usecase\patch_1024\Images\\"

In [36]:
copy_images_and_annot_dir(annot_dir,img_dir,save_annot_dir,save_img_dir,only_copy="image")

lenght annot_name_list :  844
------done-----
empyt annot 0: 
[]
image not found 0 : 
[]


([], [])

In [ ]:
        
img_dir= r"D:\UserData\z004k7nr\OneDrive - Siemens AG\neom_2\work\data\trackout_data\annotation\temp\imgs"
annot_dir =r"D:\UserData\z004k7nr\OneDrive - Siemens AG\neom_2\work\data\trackout_data\annotation\temp\annot"

save_annot_dir =r"D:\temp_save\sahi\final_test\annot\\" 
save_img_dir=r"D:\temp_save\sahi\final_test\imgs\\"

In [2]:
l = []
if l==[]:
    print('xml')
for i in l:
    print(i)

In [ ]:
# images shape

In [3]:
import glob
import cv2
img_dir = r"D:\UserData\z004k7nr\OneDrive - Siemens AG\General\data\Data Annotations\UC 1 - Trackout Detection\v1\combined_v1_demo\images"

In [5]:
img_path_list = glob.glob(img_dir+"/*")
print("len img_path_list : ",len(img_path_list[0]))
print("img_path_list : ",img_path_list[0])

len img_path_list :  155
img_path_list :  D:\UserData\z004k7nr\OneDrive - Siemens AG\General\data\Data Annotations\UC 1 - Trackout Detection\v1\combined_v1_demo\images\DJI_20211123144914_0002_W.JPG


In [ ]:
img_name

In [1]:
annot_dir =r"D:\work\trackout\usecase\patch_1024\temp_xml"

In [2]:
def get_empty_xml(annot_dir): 
    import xml.etree.ElementTree as ET
    import glob    
    empty_file_list =[]
    for xml_file_path in glob.glob(annot_dir+"\*.xml"):

        tree = ET.parse(xml_file_path)
        root = tree.getroot()
        elements = root.findall('object')
        if elements==[]:
            empty_file_list.append(xml_file_path)
            
    return empty_file_list

  

In [3]:
get_empty_xml(annot_dir)

['D:\\work\\trackout\\usecase\\patch_1024\\temp_xml\\DJI_20220421134855_0022_5740_0_6764_1024.xml',
 'D:\\work\\trackout\\usecase\\patch_1024\\temp_xml\\DJI_20220421134855_0022_5740_820_6764_1844.xml',
 'D:\\work\\trackout\\usecase\\patch_1024\\temp_xml\\DJI_20220421134855_0022_6560_0_7584_1024.xml',
 'D:\\work\\trackout\\usecase\\patch_1024\\temp_xml\\DJI_20220421134913_0024_5740_2460_6764_3484.xml',
 'D:\\work\\trackout\\usecase\\patch_1024\\temp_xml\\DJI_20220927102530_0038_3280_0_4304_1024.xml',
 'D:\\work\\trackout\\usecase\\patch_1024\\temp_xml\\DJI_20220927102530_0038_3280_2460_4304_3484.xml',
 'D:\\work\\trackout\\usecase\\patch_1024\\temp_xml\\DJI_20220927102530_0038_4100_0_5124_1024.xml',
 'D:\\work\\trackout\\usecase\\patch_1024\\temp_xml\\DJI_20220928172749_0081_6560_0_7584_1024.xml',
 'D:\\work\\trackout\\usecase\\patch_1024\\temp_xml\\DJI_20220928172749_0081_7168_0_8192_1024.xml',
 'D:\\work\\trackout\\usecase\\patch_1024\\temp_xml\\DJI_20220928172759_0082_6560_4100_7584_

In [18]:
for xml_file_path in glob.glob(annot_dir+"\*.xml"):
    empty_file_list =[]
    tree = ET.parse(xml_file_path)
    root = tree.getroot()
    if get_elements(root, 'object')==[]:
        empty_file_list.append(xml_file_path)
    for obj in get_elements(root, 'object'):
#         bndbox = get_element(obj, 'bndbox').list
# #         int(get_element(bndbox, 'xmin').text)
#         print(bndbox)
# #         if bndbox==[]
# #         print(xml_file_path)
#         break
        pass

empty_file_list  

[]

In [ ]:
for obj in get_elements(root, 'object'):
            # annotation: category_id
            category = get_element(obj, 'name').text
            if category not in PRE_DEFINE_CATEGORIES:
                new_id = len(PRE_DEFINE_CATEGORIES) + 1 -sub_id
                PRE_DEFINE_CATEGORIES[category] = new_id
#                 if category in ['water_tank', 'effluent_tank', 'fuel_tank']:
#                     print("xml_fileName : ",xml_fileName)
            category_id = PRE_DEFINE_CATEGORIES[category]
            

            # annotation: id
            bbox_id += 1

            # annotation: bbox
            bndbox = get_element(obj, 'bndbox')